Mostra in OANDA o IBKR come funziona

In [ ]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
plt.style.use("seaborn")

In [ ]:
# WITH OANDA
import tpqoa
api = tpqoa.tpqoa("oandaMY.cfg")

In [ ]:
# WITH IBKR
# ib.disconnect()
import pandas as pd
from ib_insync import *
util.startLoop()  # not necessary in scripts
ib = IB()
ib.connect()

In [ ]:
# WITH OANDA
df = api.get_history(instrument = "EUR_USD", start = "2021-09-24", end = "2024-09-24", granularity = "H8", price = "M")
# we change the column names to match IBKR
df.rename(columns={"o":"open","h":"high","l":"low","c":"close","time":"date"},inplace=True)
df.index.names = ['date']
df = df.close.to_frame()
df.head(5)

In [ ]:
# WITH IBKR
df = pd.DataFrame(ib.reqHistoricalData( Forex("EURUSD"), endDateTime = "20240924 00:00:00", 
                                  barSizeSetting="8 hours", durationStr="4 Y", 
                                  whatToShow= "MIDPOINT", useRTH = True, formatDate=2 )).set_index("date")
df.index=pd.to_datetime(df.index)
df = df.close.to_frame()
df.head(5)

In [ ]:
df.info()

In [ ]:
df.close.plot()

# Ottimizzare la strategia

# Costi di trading

Abbiamo due costi di trading. 
1. una commissione che viene caricata dal broker. Questa solitamente è in percentuale ma con un minimo e un massimo, ad esempio 0.15% del controvalore acquistato con un minimo di 2 euro e un massimo di 18 euro. 
2. il fatto che in teoria noi dovremmo sempre comprare al prezzo ask e vendere al prezzo bid. Però per semplicità abbiamo considerato sempre il prezzo bid. Ad ogni transazione ci perdiamo mezzo spread. Consideriamo però che nelle strategie in cui non c'è la posizione neutrale ma si passa da quella long a quella short e viceversa sono di fatto due transazioni e quindi ad ogni cambio perdiamo l'intero spread

Come li calcoliamo:
1. Per questo costo prevediamo una percentuale senza considerare minimi e massimi che rendono i calcoli dipendenti da quanto stiamo investendo. Al momento ne teniamo conto nelle formula usando la variabile comm, ma la mettiamo a 0. 
2. Per questo costo consideriamo che lo spread medio su euro dollaro è di 0.00008 dollari e lo dividiamo per il prezzo medio del dollaro in euro, in modo da ottenere il costo in percentuale.

In [ ]:
comm=0.0
spread=0.00002/df.close.mean() 
# attenzione che 0.00011 è in dollari e df.close è in dollari. Ottimo. 
# Controllare sempre che i termini del rapporto usino la stessa unità di misura!

Questi costi scattano tutte le volte in cui facciamo una transazione. Confrontiamo la posizione (spostata di 1 giorno) con quella precedente (spostata di 2 giorni). 

In [ ]:
comm=0.0002 # commissions of IBKR is 0.00002 with a minimum of 2 USD (which means at least 100k to have 0.00002), we make 0,0002 for 10k
